# Scrapper avec Scrapy

Scrapy est une autre manière de récupérer de l'information sur internet. Il s'agit de réaliser une araignée (Spyder en anglais) qui va "crawler" les pages les unes après les autres. 

Vous lui donnez un lien, l'araignée s'y déplace, si elle rencontre un autre lien, elle change de page et ainsi de suite. Avec ça, on peut rapidement avoir beaucoup de données et trouver des liens entre les choses. C'est parfait si on veut par exemple faire du référencement. Si vous voulez connaitre le réseau de quelqu'un sur linkedin, Scrapy est fait pour vous.

Comparé à BeautifulSoup, qui est finalement juste un parser des pages HTML, les possibilités sont très grandes ! Par contre la syntaxe est un peu plus complexe.

Pour savoir lequel choisir >> http://www.discoversdk.com/blog/beautifulsoup4-vs-scrapy

Et pour dire la vérité, les deux sont plutot complémentaires. 

## Lancer Scrapy

Scrapy ne fonctionne pas très bien dans un notebook mais on va quand même faire avec (l'usage est plutôt est d'avoir un .py qu'on lance depuis la console)

In [1]:
! pip install scrapy

    100% |████████████████████████████████| 256kB 2.6MB/s ta 0:00:01
    100% |████████████████████████████████| 3.0MB 444kB/s ta 0:00:0111
    100% |████████████████████████████████| 174kB 3.1MB/s ta 0:00:01
    100% |████████████████████████████████| 81kB 3.8MB/s ta 0:00:011
    100% |████████████████████████████████| 61kB 4.5MB/s ta 0:00:011
    100% |████████████████████████████████| 71kB 4.6MB/s ta 0:00:011
  Running setup.py bdist_wheel for PyDispatcher ... done
  Stored in directory: /home/atheane/.cache/pip/wheels/86/02/a1/5857c77600a28813aaf0f66d4e4568f50c9f133277a4122411
  Running setup.py bdist_wheel for Twisted ... done
  Stored in directory: /home/atheane/.cache/pip/wheels/91/c7/95/0bb4d45bc4ed91375013e9b5f211ac3ebf4138d8858f84abbc
Successfully built PyDispatcher Twisted


### Le détail d'une spider : 

On passe forcément par la définition d'une classe, issue de scrapy.Spider. 
On lui donne : 
- un nom "name" 
- une ou plusieurs urls de départ "start_urls"

Puis on définit une fonction qui va parser les différentes pages. 

C'est là qu'on indique si on parse ou non le contenu, on fait des tests pour le parser que ce qui nous intéresse

Dans l'exemple qui suit, on va s'intéresser à la page d'accueil de www.pythonprogramming.net

On va essayer de récupérer tous les titres des vignettes qu'on voit (il y en a 6)

<img src="./home_pythonprogramming.png"/>

Dans le code source, on remarque que les vignettes s'écrivrent de la manière suivante : 


Ce qu'on veut aller chercher "Learn how to use Python with Pandas, Matplotlib, and other modules to gather insights from and about your data." est dans une classe CSS "card-content". 
Il faut lui indiquer ces éléments là en utilisant les méthodes .css  (ou xpath qui utilise une autre syntaxe)

### Le code de première Spider : 

In [1]:
import scrapy
from scrapy.crawler import CrawlerProcess

class Content_Spider(scrapy.Spider):
    name = 'pocket_spider'
    start_urls = ['https://pythonprogramming.net/']

    def parse(self, response):
        title_list = []
        for e in response.css('div.card-panel.hoverable'):
            title_list.append(e.css('p::text').extract()[0])
        print(title_list)

### Lancer la spider

In [2]:
process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'
})

process.crawl(Content_Spider)
process.start(stop_after_crawl=True)

2017-10-17 11:36:59 [scrapy.utils.log] INFO: Scrapy 1.4.0 started (bot: scrapybot)
2017-10-17 11:36:59 [scrapy.utils.log] INFO: Overridden settings: {'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'}
2017-10-17 11:37:00 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.logstats.LogStats']
2017-10-17 11:37:00 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
 'scrapy.downloadermiddlewares.downloadtimeout.DownloadTimeoutMiddleware',
 'scrapy.downloadermiddlewares.defaultheaders.DefaultHeadersMiddleware',
 'scrapy.downloadermiddlewares.useragent.UserAgentMiddleware',
 'scrapy.downloadermiddlewares.retry.RetryMiddleware',
 'scrapy.downloadermiddlewares.redirect.MetaRefreshMiddleware',
 'scrapy.downloadermiddlewares.httpcompression.HttpCompressionMiddleware',
 'sc

Remarque : après avoir lancé une spider, il vous faudra relancer le noyau à cause de cette erreur : ReactorNotRestartable: 

    
-   Dans un notebook : Cliquer sur Kernel > Restart ou utilisez le raccourci 0,0 (la cellule en cours doit avoir une lisère bleue, puis vous appuyez deux fois sur la touche où est le 0 - sans appuyer sur majuscule. Sur un pc , vous appuyez deux fois sur le à)
-   Sur Spyder : Ctrl+.

### Exercice 1

Reprenez le premier exemple celui sur www.pythonprogramming.net. Comment feriez-vous pour enregistrer les titres des vignettes dans un json ?

### Exercice 1 - Correction 

In [1]:
import scrapy
from scrapy.crawler import CrawlerProcess

class PythonItem(scrapy.Item):
    # define the fields for your item here like:
    # name = scrapy.Field()
    name = scrapy.Field()

class Content_Spider(scrapy.Spider):
    name = 'pocket_spider'
    start_urls = ['https://pythonprogramming.net/']

    custom_settings = {'FEED_FORMAT' : 'jsonlines',
                        'FEED_URI' : 'python_vignettes.json', 
                       # le nom du fichier json dépend du moment où on lance le code
                        'FEED_EXPORT_ENCODING' : 'utf-8' }    
    
    def parse(self, response):
        for e in response.css('div.card-panel.hoverable'):
            yield PythonItem(
                name = e.css('p::text').extract_first()
            )

In [2]:
process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'
})

process.crawl(Content_Spider)
process.start(stop_after_crawl=True)

2017-10-16 12:08:11 [scrapy.utils.log] INFO: Scrapy 1.4.0 started (bot: scrapybot)
2017-10-16 12:08:11 [scrapy.utils.log] INFO: Overridden settings: {'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'}
2017-10-16 12:08:11 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.feedexport.FeedExporter',
 'scrapy.extensions.logstats.LogStats']
2017-10-16 12:08:11 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
 'scrapy.downloadermiddlewares.downloadtimeout.DownloadTimeoutMiddleware',
 'scrapy.downloadermiddlewares.defaultheaders.DefaultHeadersMiddleware',
 'scrapy.downloadermiddlewares.useragent.UserAgentMiddleware',
 'scrapy.downloadermiddlewares.retry.RetryMiddleware',
 'scrapy.downloadermiddlewares.redirect.MetaRefreshMiddleware',
 'scrapy.downloadermiddlewares.ht

### Exercice 2

Comment feriez-vous pour que la spider se déplace sur tous les liens internes à partir du premier lien donné ? Inspirez-vous de [cet exemple](https://doc.scrapy.org/en/latest/intro/tutorial.html#following-links).

### Exercice 2 - correction

In [1]:
import scrapy
from scrapy.crawler import CrawlerProcess
    
class Content_Spider(scrapy.Spider):
    name = 'pocket_spider'
    start_urls = ['https://pythonprogramming.net/']

    custom_settings = {'FEED_FORMAT' : 'jsonlines',
                        'FEED_URI' : 'python_vignettes_follow.json', 
                       # le nom du fichier json dépend du moment où on lance le code
                        'FEED_EXPORT_ENCODING' : 'utf-8' }    
    
    def parse(self, response):
        for e in response.css('div.card-panel.hoverable'):
            print(e.css("strong::text").extract_first())
            yield {
                "name" : e.css("p::text").extract_first()
            }
        for a in response.css('div.card-panel.hoverable a::attr(href)').extract():
            print(a)
            if a is not None:
                yield response.follow(a, callback=self.parse)            

In [2]:
process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'
})

process.crawl(Content_Spider)
process.start(stop_after_crawl=True)

2017-10-16 17:24:28 [scrapy.utils.log] INFO: Scrapy 1.4.0 started (bot: scrapybot)
2017-10-16 17:24:28 [scrapy.utils.log] INFO: Overridden settings: {'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'}
2017-10-16 17:24:28 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.feedexport.FeedExporter',
 'scrapy.extensions.logstats.LogStats']
2017-10-16 17:24:28 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
 'scrapy.downloadermiddlewares.downloadtimeout.DownloadTimeoutMiddleware',
 'scrapy.downloadermiddlewares.defaultheaders.DefaultHeadersMiddleware',
 'scrapy.downloadermiddlewares.useragent.UserAgentMiddleware',
 'scrapy.downloadermiddlewares.retry.RetryMiddleware',
 'scrapy.downloadermiddlewares.redirect.MetaRefreshMiddleware',
 'scrapy.downloadermiddlewares.ht

Data Analysis
Robotics
Web Development
Game Development
Python Fundamentals
GUIs
/data-analysis-tutorials/
/robotics-tutorials/
/web-development-tutorials/
/game-development-tutorials/
/python-fundamental-tutorials/
/gui-development-tutorials/


2017-10-16 17:24:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/gui-development-tutorials/> (referer: https://pythonprogramming.net/)
2017-10-16 17:24:29 [scrapy.core.scraper] DEBUG: Scraped from <200 https://pythonprogramming.net/gui-development-tutorials/>
{'name': 'Create up-to-date looking graphical user interfaces with PyQt.'}
2017-10-16 17:24:29 [scrapy.core.scraper] DEBUG: Scraped from <200 https://pythonprogramming.net/gui-development-tutorials/>
{'name': 'Tkinter, part of the Python standard library, can be used to create simple GUI applications.'}
2017-10-16 17:24:29 [scrapy.core.scraper] DEBUG: Scraped from <200 https://pythonprogramming.net/gui-development-tutorials/>
{'name': "Create cross-platform (Windows, Mac, Linux, iOS, and Android) games and applications with Python's Kivy."}
2017-10-16 17:24:29 [scrapy.dupefilters] DEBUG: Filtered duplicate request: <GET https://pythonprogramming.net/basic-gui-pyqt-tutorial/> - no more duplicates wil

PyQt
Tkinter
Kivy Basics
/basic-gui-pyqt-tutorial/
/basic-gui-pyqt-tutorial/
/tkinter-depth-tutorial-making-actual-program/
/tkinter-depth-tutorial-making-actual-program/
/kivy-application-development-tutorial/
/kivy-application-development-tutorial/


2017-10-16 17:24:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/kivy-application-development-tutorial/> (referer: https://pythonprogramming.net/gui-development-tutorials/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/python-fundamental-tutorials/> (referer: https://pythonprogramming.net/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/robotics-tutorials/> (referer: https://pythonprogramming.net/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/data-analysis-tutorials/> (referer: https://pythonprogramming.net/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/web-development-tutorials/> (referer: https://pythonprogramming.net/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/game-development-tutorials/> (refere

Basics
Intermediate Python Fundamentals
/introduction-to-python-programming/
/introduction-to-python-programming/
/introduction-intermediate-python-tutorial/
/introduction-intermediate-python-tutorial/
Raspberry Pi Tutorials
(Basic) Learn to program with the Raspberry Pi
(Intermediate) Build and program a Quadcopter
/introduction-raspberry-pi-tutorials/
/introduction-raspberry-pi-tutorials/
/robotics-raspberry-pi-tutorial-gopigo-introduction/
/robotics-raspberry-pi-tutorial-gopigo-introduction/
/building-quadcopter-tutorial-intro/
/building-quadcopter-tutorial-intro/
Machine Learning
Data Analysis w/ Pandas
Data Visualization
Finance
Google Cloud Tutorials
Image and Video Analysis
Distributed Computing
Natural Language Processing
/machine-learning-tutorials/
/data-analysis-python-pandas-tutorial-introduction/
/data-analysis-python-pandas-tutorial-introduction/
/matplotlib-intro-tutorial/
/matplotlib-intro-tutorial/
/finance-tutorials/
/virtual-machine-google-cloud-tutorial/
/virtual-ma

2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/introduction-to-python-programming/> (referer: https://pythonprogramming.net/python-fundamental-tutorials/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/building-quadcopter-tutorial-intro/> (referer: https://pythonprogramming.net/robotics-tutorials/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/robotics-raspberry-pi-tutorial-gopigo-introduction/> (referer: https://pythonprogramming.net/robotics-tutorials/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/introduction-raspberry-pi-tutorials/> (referer: https://pythonprogramming.net/robotics-tutorials/)
2017-10-16 17:24:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/build-supercomputer-raspberry-pi/> (referer: https://pythonprogramming.net/data-analysis-tutoria

Python for Finance
Support Vector Machines with Scikit Learn
/getting-stock-prices-python-programming-for-finance/
/getting-stock-prices-python-programming-for-finance/
/machine-learning-python-sklearn-intro/
/machine-learning-python-sklearn-intro/
Practical Machine Learning with Python
Python Plays GTA V
TensorFlow Object Detection
Support Vector Machines with Scikit Learn
Clustering (unsupervised machine learning)
Image recognition w/ basic Pattern Recognition
/machine-learning-tutorial-python-introduction/
/machine-learning-tutorial-python-introduction
/game-frames-open-cv-python-plays-gta-v/
/game-frames-open-cv-python-plays-gta-v/
/introduction-use-tensorflow-object-detection-api-tutorial/
/introduction-use-tensorflow-object-detection-api-tutorial/
/machine-learning-python-sklearn-intro/
/machine-learning-python-sklearn-intro/
/flat-clustering-machine-learning-python-scikit-learn/
/flat-clustering-machine-learning-python-scikit-learn/
/image-recognition-python/
/image-recognition-

2017-10-16 17:24:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/introduction-use-tensorflow-object-detection-api-tutorial/> (referer: https://pythonprogramming.net/machine-learning-tutorials/)
2017-10-16 17:24:31 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://pythonprogramming.net/machine-learning-tutorial-python-introduction/> from <GET https://pythonprogramming.net/machine-learning-tutorial-python-introduction>
2017-10-16 17:24:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/flat-clustering-machine-learning-python-scikit-learn/> (referer: https://pythonprogramming.net/machine-learning-tutorials/)
2017-10-16 17:24:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogramming.net/game-frames-open-cv-python-plays-gta-v/> (referer: https://pythonprogramming.net/machine-learning-tutorials/)
2017-10-16 17:24:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://pythonprogram

### Une spider plus complexe

Dans ce cas ci, on va essayer de récupérer des informations sur le site de ikea.com, on veut obtenir toutes les informations sur les produits les meilleurs marchés (ceux qui sont "des bonnes affaires"). 

Leur prix est  indiqué dans une étiquette jaune. 

<img src="./ikea_vasnas.png"/>

Dans le code source, ça se traduit par la présence d'un champ avec le terme  __productBtiBack__ (BTI - Breath-Taking Itemp)

L'origine de ce que vous verrez ici est disponible à cette adresse https://github.com/ThunderEX/ikea_bti

In [1]:
import locale
import scrapy
from scrapy.crawler import CrawlerProcess
from scrapy.spiders import SitemapSpider

On commence par définir les différents éléments qu'on voudra récupérer dans une classe

In [2]:
class IkeaBtiItem(scrapy.Item):
    # define the fields for your item here like:
    # name = scrapy.Field()
    name = scrapy.Field()
    product_type = scrapy.Field()
    package_price = scrapy.Field()
    url = scrapy.Field()

On indique ici le comportement de la spider. 

On utilise la classe Sitemap, qui utilise le plan du site (qui sert habituellement aux scrapers de référencement). C'est ce qui va nous permettre de visiter tout le site.  

On lui indique donc le sitemap comme site de départ, on lui dit de regarder les pages qui du domaine fr_FR et celles qui ont le mot "products" dans leur url. En clair, ça donne tous les produits du catalogue français de ikea. 

On ajoute 3 paramètres qui nous permettent d'enregistrer ce qui sort de la classe scrapy.Item dans un json et le tour est joué. 

En très peu de lignes de code, on peut visiter plus de 30 000 pages de produits ikea et enregistrer dans un json les produits qui nous intéressent. 

In [3]:
class BtiSpider(SitemapSpider):
    name = "bti"
    sitemap_urls = ['http://www.ikea.com/sitemap.xml']
    sitemap_follow = ['/sitemap/fr_FR/']
    sitemap_rules = [
        (r'.*/products/', 'parse_product_page'),
    ]
    custom_settings = {'FEED_FORMAT' : 'jsonlines',
                        'FEED_URI' : 'res/%(name)s_%(time)s.json', 
                       # le nom du fichier json dépend du moment où on lance le code
                        'FEED_EXPORT_ENCODING' : 'utf-8' }

    def parse_product_page(self, response):
        div = response.xpath('//div[contains(@class, "productBtiFront")]')
        if div:
            div = div[0]
            yield IkeaBtiItem(
                name=div.xpath('.//div[contains(@class, "productName")]/text()').extract_first().strip(),
                product_type=div.xpath('.//div[contains(@class, "productType")]/text()').extract_first().strip(),
                package_price=''.join(e for e in div.xpath('.//span[contains(@class, "packagePrice")]/text()').extract()).strip().replace(u'\xa0', u' '),
                url=response.url,
            )

Attention, le code ci-dessous prend 1heure à s'exécuter. Le temps de visiter tous les produits d'ikéa. On l'a fait tourner pour vous et le fichier complet est "./all_bti_ikea.json"

In [4]:
BtiSpider.sitemap_follow = ['/sitemap/%s/' % locale.getdefaultlocale()[0]]

process = CrawlerProcess({ 'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)' })

process.crawl(BtiSpider)
process.start()  # tant que l'araignée est en train de se promener, le noyeau ipython est occupé.
#Il s'arrêtera quand la spider aura fini de tout explorer


2017-10-15 18:25:42 [scrapy.utils.log] INFO: Scrapy 1.4.0 started (bot: scrapybot)
2017-10-15 18:25:42 [scrapy.utils.log] INFO: Overridden settings: {'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'}
2017-10-15 18:25:42 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.feedexport.FeedExporter',
 'scrapy.extensions.logstats.LogStats']
2017-10-15 18:25:42 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
 'scrapy.downloadermiddlewares.downloadtimeout.DownloadTimeoutMiddleware',
 'scrapy.downloadermiddlewares.defaultheaders.DefaultHeadersMiddleware',
 'scrapy.downloadermiddlewares.useragent.UserAgentMiddleware',
 'scrapy.downloadermiddlewares.retry.RetryMiddleware',
 'scrapy.downloadermiddlewares.redirect.MetaRefreshMiddleware',
 'scrapy.downloadermiddlewares.httpcompression.HttpCompressionMiddleware',
 

2017-10-15 18:26:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S39158792/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S99158893/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S59124452/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S49124443/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S39124448/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:28 [scra

2017-10-15 18:26:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S49169016/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S99169014/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S69169015/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S89169019/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S09169004/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:34 [scra

2017-10-15 18:26:36 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S89165139/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_5.xml)
2017-10-15 18:26:36 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/catalog/categories/departments/bedroom/> from <GET http://www.ikea.com/fr/fr/catalog/products/S49165235/>
2017-10-15 18:26:36 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S39158985/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_5.xml)
2017-10-15 18:26:36 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/40332564/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.xml)
2017-10-15 18:26:36 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S79219524/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_4.x

2017-10-15 18:26:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/30315391/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_2.xml)
2017-10-15 18:26:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/70360334/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_2.xml)
2017-10-15 18:26:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/70342199/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_2.xml)
2017-10-15 18:26:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/20322066/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_2.xml)
2017-10-15 18:26:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/60322984/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_2.xml)
2017-10-15 18:26:37 [scrapy.co

...

2017-10-15 19:40:06 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/catalog/categories/departments/bedroom/10681/> from <GET http://www.ikea.com/fr/fr/catalog/products/10145837/>
2017-10-15 19:40:06 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/catalog/categories/departments/small_storage/> from <GET http://www.ikea.com/fr/fr/catalog/products/20246162/>
2017-10-15 19:40:07 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S09201706/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_15.xml)
2017-10-15 19:40:08 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S29190429/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_15.xml)
2017-10-15 19:40:08 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S59207310/> (referer: http://www.ikea.

2017-10-15 19:40:09 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/catalog/categories/departments/bedroom/10681/> from <GET http://www.ikea.com/fr/fr/catalog/products/30149957/>
2017-10-15 19:40:09 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/50308455/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_14.xml)
2017-10-15 19:40:09 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/50149956/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_14.xml)
2017-10-15 19:40:09 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/catalog/categories/departments/bedroom/10681/> from <GET http://www.ikea.com/fr/fr/catalog/products/00149954/>
2017-10-15 19:40:09 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S89201689/> (referer: http://www.ikea.co

2017-10-15 19:40:10 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/10207057/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_16.xml)
2017-10-15 19:40:10 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S09218467/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_16.xml)
2017-10-15 19:40:10 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/> from <GET http://www.ikea.com/fr/fr/catalog/products/S89189989/>
2017-10-15 19:40:10 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/> from <GET http://www.ikea.com/fr/fr/catalog/products/S99189984/>
2017-10-15 19:40:10 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/> from <GET http://www.ikea.com/fr/fr/catalog/products/S29189987/>
2017-10-15 19:40:10 [scrapy.downloadermiddlewares.r

2017-10-15 19:40:20 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S39189901/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_16.xml)
2017-10-15 19:40:20 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S89189913/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_16.xml)
2017-10-15 19:40:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S29192895/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_14.xml)
2017-10-15 19:40:21 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/catalog/categories/departments/living_room/12150/> from <GET http://www.ikea.com/fr/fr/catalog/products/S59189919/>
2017-10-15 19:40:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S49189868/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Pro

2017-10-15 19:40:24 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET http://www.ikea.com/fr/fr/> from <GET http://www.ikea.com/fr/fr/catalog/products/S49188963/>
2017-10-15 19:40:24 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://www.ikea.com/fr/fr/catalog/products/S79192826/> (referer: http://www.ikea.com/sitemap/fr_FR/siteMap_Product_fr_FR_14.xml)
2017-10-15 19:40:24 [scrapy.core.engine] INFO: Closing spider (finished)
2017-10-15 19:40:24 [scrapy.extensions.feedexport] INFO: Stored jsonlines feed (163 items) in: res/bti_2017-10-15T16-25-42.json
2017-10-15 19:40:24 [scrapy.statscollectors] INFO: Dumping Scrapy stats:
{'downloader/request_bytes': 95243606,
 'downloader/request_count': 35861,
 'downloader/request_method_count/GET': 35861,
 'downloader/response_bytes': 1431958320,
 'downloader/response_count': 35861,
 'downloader/response_status_count/200': 34622,
 'downloader/response_status_count/301': 1227,
 'downloader/response_status_count/404': 12,
 'd

### Exercice 1 

A partir du .json généré par ce code "./all_bti_ikea.json", quel produit est le plus cher ?

In [ ]:
import pandas

data_ikea_bti = pandas.read_json("res/all_bti_ikea.json",lines=True, encoding='utf-8')
data_ikea_bti.head()

In [41]:
data_ikea_bti['package_price'] = data_ikea_bti['package_price'].str.replace('€','')
data_ikea_bti['package_price'] = data_ikea_bti['package_price'].str.replace(',','.').convert_objects(convert_numeric=True)
data_ikea_bti['package_price'].head()


2017-10-15 20:57:26 [py.warnings] WARNING: C:\Users\Houston\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  Use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  



0    4.50
1    3.99
2    6.99
3    1.50
4    0.50
Name: package_price, dtype: float64

In [44]:
data_ikea_bti.loc[data_ikea_bti['package_price'].idxmax()]

name                                                         LAGAN
package_price                                                  299
product_type                   Réfrigérateur/congélateur A+, blanc
url              http://www.ikea.com/fr/fr/catalog/products/102...
Name: 53, dtype: object

In [45]:
data_ikea_bti.loc[data_ikea_bti['package_price'].idxmin()]

name                                                        VÄSNAS
package_price                                                 0.39
product_type                         Photophore, verre transparent
url              http://www.ikea.com/fr/fr/catalog/products/602...
Name: 17, dtype: object